Thanks to @illided

In [68]:
from typing import List

import numpy as np
import pandas as pd

import plotly.express as px
from tqdm import tqdm

In [78]:
# strategy = 1 ---> explicit
# strategy = 2 ---> non_explicit
def solve_heat_equation(
        strategy: int = 1,
        f=lambda x, t: 0,
        left=lambda t: 0,
        right=lambda t: 0,
        initial=lambda x: 0,
        a: float = 1,
        x_segments_num: int = 100,
        time_segments_num: int = 100,
        T: float = 10,
        k: float = 1
):
    n = x_segments_num
    x_range = np.linspace(0, a, x_segments_num)
    h = x_range[1] - x_range[0]
    time_range = np.linspace(0, T, time_segments_num)
    tau = time_range[1] - time_range[0]

    if strategy == 1 and 2 * k * tau > h ** 2:
        print("For equation stability must be: 2kt <= h**2")

    if strategy == 1:
        layers = solve_with_explicit_schema(T, tau, k, h, time_segments_num, x_range, initial, left, right, f)
    else:
        layers = solve_with_non_explicit_schema(T, tau, k, h, n, time_segments_num, x_range, initial, left, right, f)

    plot_heatmap(layers)


def solve_with_explicit_schema(T, tau, k, h, time_segments_num, x_range, initial, left, right, f):
    def get_next_layer(time) -> List[float]:
        u_first = left(time)
        new_layer = [u_first]
        prev_layer = layers[-1]

        for i, x in list(enumerate(x_range))[1:-1]:
            u_c = prev_layer[i - 1] - 2 * prev_layer[i] + prev_layer[i + 1]
            u_n = tau * ((k / h ** 2) * u_c + f(x, time)) + prev_layer[i]
            new_layer.append(u_n)

        u_last = right(time)
        new_layer.append(u_last)
        return new_layer

    layers = [[initial(x) for x in x_range]]
    for time in tqdm(np.linspace(0, T, time_segments_num)[1:], leave=False):
        layers.append(get_next_layer(time))
    return layers


def solve_with_non_explicit_schema(T, tau, k, h, n, time_segments_num, x_range, initial, left, right, f):
    def generate_S_matrix(n):
        a = - k / h ** 2
        b = 1 / tau + 2 * k / h ** 2

        first_row = np.zeros(n)
        first_row[0] = b
        first_row[1] = a
        S = [first_row]

        for i in range(n - 2):
            row = np.zeros(n)
            row[i] = a
            row[i + 1] = b
            row[i + 2] = a
            S.append(row)

        last_row = np.zeros(n)
        last_row[n - 2] = a
        last_row[n - 1] = b
        S.append(last_row)

        return np.array(S)

    def get_next_layer(time):
        S = generate_S_matrix(n - 2)

        u_first = left(time)
        u_last = right(time)
        prev_layer = layers[-1]

        b = np.zeros(n - 2)

        koef = k / h ** 2

        b[0] = prev_layer[1] / tau + f(x_range[1], time + tau) + u_first * koef
        b[n - 3] = prev_layer[-2] / tau + f(x_range[-2], time + tau) + u_last * koef

        for i, x in list(enumerate(x_range))[2:-2]:
            b[i - 1] = prev_layer[i] / tau + f(x, time + tau)

        solution = np.linalg.solve(S, b)
        return [u_first, *solution, u_last]

    layers = [[initial(x) for x in x_range]]
    for time in tqdm(np.linspace(0, T, time_segments_num)[1:], leave=False):
        layers.append(get_next_layer(time))
    return layers


def plot_lines(time_range, n, layers):
    x_label = "x"
    y_label = "t"
    color_label = "label"
    data = []
    for x, y in zip(time_range, [left(t) for t in time_range]):
        data.append([x, y, "Left"])
    for x, y in zip(time_range, [right(t) for t in time_range]):
        data.append([x, y, "Right"])
    for x, y in zip(time_range, [layer[n // 2] for layer in layers]):
        data.append([x, y, "Median"])
    df = pd.DataFrame(data, columns=[x_label, y_label, color_label])
    fig = px.line(df, x=x_label, y=y_label, color=color_label)
    fig.show()


def plot_heatmap(layers):
    fig = px.imshow(np.array(list(reversed(layers))))
    fig.show()

In [81]:
right = lambda t: 20 + np.sin(t) * 10
left = lambda t: 20
f = lambda x, t: 0
initial = lambda x: 20
solve_heat_equation(strategy=2, left=left, right=right, k=0.1, x_segments_num=100, time_segments_num=100, f=f,
                    initial=initial)

In [82]:
right = lambda t: -abs(t - 5) + 10
left = lambda t: 5
f = lambda x, t: 0
initial = lambda x: 5
solve_heat_equation(strategy=2, left=left, right=right, k=1, x_segments_num=100, time_segments_num=100, f=f,
                    initial=initial)

In [83]:
right = lambda t: np.cos(t)
left = lambda t: np.sin(t)
f = lambda x, t: -t
initial = lambda x: 0
solve_heat_equation(strategy=2, left=left, right=right, k=0.5, x_segments_num=100, time_segments_num=100, f=f,
                    initial=initial)

In [84]:
right = lambda t: np.sign(np.cos(t))
left = lambda t: np.sign(np.sin(t))
f = lambda x, t: 0
initial = lambda x: (1 - x) * left(0) + x * right(0)
solve_heat_equation(strategy=2, left=left, right=right, k=0.5, x_segments_num=100, time_segments_num=100, f=f,
                    initial=initial)

In [85]:
right = lambda t: 20 + np.sin(t) * 10
left = lambda t: 20
f = lambda x, t: 0
initial = lambda x: 20
solve_heat_equation(strategy=1, left=left, right=right, k=0.1, x_segments_num=100, time_segments_num=1000, f=f,
                    initial=initial)

For equation stability must be: 2kt <= h**2


  0%|          | 0/999 [00:00<?, ?it/s]/tmp/ipykernel_10958/694747257.py:41: RuntimeWarning:

overflow encountered in double_scalars

/tmp/ipykernel_10958/694747257.py:41: RuntimeWarning:

invalid value encountered in double_scalars

